In [55]:
data_directory="data"#"path/to/data"
directory="/Users/amaiasagastimartinez/Desktop/SENS-Soundlights/code/sens-sensor"#"path/to/sens-sensor"
print(f"Data directory is {data_directory}")
print(f"Working directory is {directory}")

Data directory is data
Working directory is /Users/amaiasagastimartinez/Desktop/SENS-Soundlights/code/sens-sensor


In [56]:
import pandas as pd
import os
import random
import json

# Set the working directory
os.chdir(directory)

# Imports from this project
from CLAP.src.laion_clap import CLAP_Module
from development.lib.auxiliars import (
    clap_features,
)


We want to incorporate 1000 audios from IDMT audios to US8k dataset, 100 to each of the 10 folds. For that, we will select 1000 random audios and calculate the CLAP embeddings. We will create a CSV or JSON (a replica of UrbanSound8K_CLAP_dataset.csv or UrbanSound8K_CLAP_dataset.json). To the already existing audios from US8k we will add a column "vehicles_idmt" with values zero. New rows corresponding to the new 1000 audios will be added feeling all sources to zero except for "vehicles_idmt" with values '1'.

## Import the generated dataset for US8k

In [57]:
df_US8k=pd.read_csv(os.path.join(data_directory,"files/UrbanSound8K_CLAP_dataset/UrbanSound8K_CLAP_dataset.csv"), delimiter=",")
print(df_US8k)

         slice_file_name    fsID       start         end  salience  fold  \
0       100032-3-0-0.wav  100032    0.000000    0.317551         1     5   
1     100263-2-0-117.wav  100263   58.500000   62.500000         1     5   
2     100263-2-0-121.wav  100263   60.500000   64.500000         1     5   
3     100263-2-0-126.wav  100263   63.000000   67.000000         1     5   
4     100263-2-0-137.wav  100263   68.500000   72.500000         1     5   
...                  ...     ...         ...         ...       ...   ...   
8727     99812-1-2-0.wav   99812  159.522205  163.522205         2     7   
8728     99812-1-3-0.wav   99812  181.142431  183.284976         2     7   
8729     99812-1-4-0.wav   99812  242.691902  246.197885         2     7   
8730     99812-1-5-0.wav   99812  253.209850  255.741948         2     7   
8731     99812-1-6-0.wav   99812  332.289233  334.821332         2     7   

      classID             class  \
0           3          dog_bark   
1           2  ch

## Add column "vehicles_IDMT" all zeros

In [58]:
# New column with source vehicle_IDMT with all zeros
df_US8k_IDMT=df_US8k.copy()
df_US8k_IDMT['vehicles_IDMT'] = 0
print(df_US8k_IDMT)

         slice_file_name    fsID       start         end  salience  fold  \
0       100032-3-0-0.wav  100032    0.000000    0.317551         1     5   
1     100263-2-0-117.wav  100263   58.500000   62.500000         1     5   
2     100263-2-0-121.wav  100263   60.500000   64.500000         1     5   
3     100263-2-0-126.wav  100263   63.000000   67.000000         1     5   
4     100263-2-0-137.wav  100263   68.500000   72.500000         1     5   
...                  ...     ...         ...         ...       ...   ...   
8727     99812-1-2-0.wav   99812  159.522205  163.522205         2     7   
8728     99812-1-3-0.wav   99812  181.142431  183.284976         2     7   
8729     99812-1-4-0.wav   99812  242.691902  246.197885         2     7   
8730     99812-1-5-0.wav   99812  253.209850  255.741948         2     7   
8731     99812-1-6-0.wav   99812  332.289233  334.821332         2     7   

      classID             class  \
0           3          dog_bark   
1           2  ch

## Choose 1000 random audios from IDMT dataset, generate features, and add them with US8k dataframe

In [59]:
# Choose 1000 random audios from list of IDMT audios

idmt_folder_path=os.path.join(data_directory, "IDMT_Traffic/audio")

# Get a list of contents in the folder
idmt_audios = os.listdir(idmt_folder_path)
# Randomize list
random.seed(0)
random.shuffle(idmt_audios)
# Select only 1000
idmt_audios=idmt_audios[0:1000]
print(len(idmt_audios))

fold=1
audios_per_fold=100

# Load the model
print("------- code starts -----------")
model = CLAP_Module(enable_fusion=True)
print("------- clap module -----------")
model.load_ckpt("data/models/630k-fusion-best.pt")
print("------- model loaded -----------")

count=0
for audio_name in idmt_audios:
    audio_path=os.path.join(idmt_folder_path, audio_name)

    # Initialize a row with zeros
    new_row = {col: 0 for col in df_US8k_IDMT.columns}

    # Add fold number
    new_row["fold"]=fold
    count=count+1
    if count==audios_per_fold: # when reached number of audios per fold
        fold=fold+1 # new fold number
        count=0

    # Add file name
    new_row["slice_file_name"]=audio_name

    # Add audio_path
    new_row["audio_path"]=audio_path

    # Class Id (11 for IDMT vehicles)
    new_row["classID"]=11

    # Class
    new_row["class"]="vehicles_IDMT"
    new_row["vehicles_IDMT"]=1

    print(new_row)
    # Generate CLAP embedding and save it to dataframe
    embedding = model.get_audio_embedding_from_filelist(
            [audio_path], use_tensor=False
    )[0]
    for i, name in enumerate(clap_features):
        new_row[name] = float(embedding[i])

    # Append the row to the DataFrame
    df_US8k_IDMT = pd.concat([df_US8k_IDMT, pd.DataFrame([new_row])], ignore_index=True)


1000
------- code starts -----------


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaModel: ['lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


------- clap module -----------
Load the specified checkpoint data/models/630k-fusion-best.pt from users.
Load Checkpoint...
logit_scale_a 	 Loaded
logit_scale_t 	 Loaded
audio_branch.spectrogram_extractor.stft.conv_real.weight 	 Loaded
audio_branch.spectrogram_extractor.stft.conv_imag.weight 	 Loaded
audio_branch.logmel_extractor.melW 	 Loaded
audio_branch.bn0.weight 	 Loaded
audio_branch.bn0.bias 	 Loaded
audio_branch.patch_embed.proj.weight 	 Loaded
audio_branch.patch_embed.proj.bias 	 Loaded
audio_branch.patch_embed.norm.weight 	 Loaded
audio_branch.patch_embed.norm.bias 	 Loaded
audio_branch.patch_embed.mel_conv2d.weight 	 Loaded
audio_branch.patch_embed.mel_conv2d.bias 	 Loaded
audio_branch.patch_embed.fusion_model.local_att.0.weight 	 Loaded
audio_branch.patch_embed.fusion_model.local_att.0.bias 	 Loaded
audio_branch.patch_embed.fusion_model.local_att.1.weight 	 Loaded
audio_branch.patch_embed.fusion_model.local_att.1.bias 	 Loaded
audio_branch.patch_embed.fusion_model.local_att

## Save new dataframe as CSV and JSON

In [67]:
# Check if the directory exists
saving_path=os.path.join(data_directory,"files/IDMT-US8k_CLAP_dataset")
if not os.path.exists(saving_path):
    # If it doesn't exist, create it
    os.makedirs(saving_path)
    print(f"Directory {saving_path} created.")


# Save as CSV
csv_file_path = os.path.join(saving_path,"IDMT-US8k_CLAP_dataset.csv")
df_US8k_IDMT.to_csv(csv_file_path, index=False)  # index=False to omit the row index
print(f"DataFrame saved as CSV: {csv_file_path}")

# Save as JSON
json_file_path = os.path.join(saving_path,"IDMT-US8k_CLAP_dataset.json")
#df_US8k_IDMT.to_json(json_file_path, orient="index", indent=4)  # 'records' for list of dictionaries, 'lines=True' for JSON lines format
with open(json_file_path, "w") as f:
    f.write(df_US8k_IDMT.to_json(orient="records", indent=4).replace("\\/", "/"))
print(f"DataFrame saved as JSON: {json_file_path}") 


DataFrame saved as CSV: data/files/IDMT-US8k_CLAP_dataset/IDMT-US8k_CLAP_dataset.csv
DataFrame saved as JSON: data/files/IDMT-US8k_CLAP_dataset/IDMT-US8k_CLAP_dataset.json
